# Fibre packer nop - first draft

*Author: Vedrana Andersen Dahl (vand@dtu.dk)*


In [1]:
import torch
import plotly.graph_objects as go
from tqdm.notebook import tqdm
import fibre_packer_nop as fp

The function for optimizing a single slice points (below) is still work in progress. Weighting of the different losses, and stopping criteria are not yet implemented.

In [2]:
def optimize_slice_points(p, radii, c, iters=200):
    delta = 0.01 * radii.mean()
    n = 3
    N = len(radii)
    min_d = fp.minimal_distance(radii)
    p.requires_grad = True
    p.to(torch_device)
    optimizer = torch.optim.Adam([p], lr=0.1)
    loss_contributions = []
    progress_bar = tqdm(range(iters), bar_format='{desc:<100}{bar}{n_fmt}/{total_fmt}')
    for iter in progress_bar:  
        optimizer.zero_grad()   
        d = fp.pairwise_distance(p)
        overlap = fp.overlap_penalty(d, min_d, delta)
        protrusion = fp.protrusion_penalty(p, radii, c)
        separation = fp.separation_penalty(d, radii, n, delta)
        loss = overlap + N * protrusion + 1/N * separation
        loss.backward()
        optimizer.step()
        loss_contributions.append((overlap.item(), N * protrusion.item(), 1/N * separation.item()))
        progress_bar.set_description(f"Overlap {overlap:.2f}, " + 
            f"protrusion {protrusion:.2f}", refresh=True)
    
    p = p.detach()
    overlap = fp.overlap_penalty(d, min_d)
    protrusion = fp.protrusion_penalty(p, radii, c)
    loss_contributions = {k:list(v) for k, v in 
            zip(['overlap', 'protrusion', 'separation'], zip(*loss_contributions))}
    return p, (overlap, protrusion), loss_contributions

Choosing the size of the problem.


In [3]:
# Parameters to decide on
domain_radius = 40  # Domain radius
fibre_radius_mean = 2  # Mean fibre radius
fibre_volume_fraction = 70  # Desired fibre volume fraction
number_slices = 20 # Number of slices to generate

# Parameters calculated from the above
fibre_radius_sigma = 0.1 * fibre_radius_mean  # Standard deviation of fibre radius - TODO repair the function 
radii = fp.initialize_radii(domain_radius, fibre_volume_fraction, fibre_radius_mean, fibre_radius_sigma)
N = len(radii)  # Number of fibres

# TODO remove legend from histogram
fp.show_radii_distribution(radii)

In [4]:
p0 = fp.initialize_slice_points(domain_radius - fibre_radius_mean, N)
fp.show_slice(p0, radii, domain_radius, title='First slice (p0) initial')

In [5]:
torch_device = fp.select_device()
p0, (overlap, protrusion), losses = optimize_slice_points(p0, radii, domain_radius)
fp.show_slice(p0, radii, domain_radius, 
    title=f'First slice (p0) optimized. Overlap {overlap:.2f}, protrusion {protrusion:.2f}')

Using device mps


                                                                                                              …

In [6]:
fp.show_losses(losses)

In [7]:
pZ = p0.clone()
pZ = fp.rotate_bundle(pZ, radii, (domain_radius/2, 0), domain_radius/2.5, -torch.pi/2)
pZ = fp.rotate_bundle(pZ, radii, (-domain_radius/2, 0), domain_radius/2, -torch.pi/3)
pZ = fp.rotate_bundle(pZ, radii, (0, 0), domain_radius, torch.pi/4)
pz = fp.swap_points(pZ)

fp.show_slice(pZ, radii, domain_radius, title='Last slice (pZ) initial')

In [8]:
pZ, (overlap, protrusion), losses = optimize_slice_points(pZ, radii, domain_radius)
fp.show_slice(pZ, radii, domain_radius, 
    title=f'Last slice (pZ) optimized. Overlap {overlap:.2f}, protrusion {protrusion:.2f}')

                                                                                                              …

In [9]:
fp.show_losses(losses)

In [10]:
configuration = fp.interpolate_configuration(p0, pZ, number_slices)
fp.show_3D_configuration(configuration, title='Initial configuration')
fp.animate_slices(configuration, radii, domain_radius, title='Initial configuration')

In [11]:
N = len(radii)
min_d = fp.minimal_distance(radii)
delta = 0.01 * radii.mean()
configuration.requires_grad = True
configuration.to(torch_device)
optimizer = torch.optim.Adam([configuration], lr=0.1)
loss_contributions = []
iters = 200
progress_bar = tqdm(range(iters), bar_format='{desc:<100}{bar}{n_fmt}/{total_fmt}')
for iter in progress_bar:  
    optimizer.zero_grad()   
    d = fp.pairwise_distance(configuration)
    overlap = fp.overlap_penalty(d, min_d, delta)
    protrusion = fp.protrusion_penalty(configuration, radii, domain_radius)
    stretching = fp.stretching_penalty(configuration)
    bending = fp.bending_penalty(configuration)
    boundary = fp.boundary_penalty(configuration, p0, pZ)
    loss = overlap + N * protrusion + 1/N * stretching + 2/N * bending + N * boundary
    loss.backward()
    optimizer.step()
    loss_contributions.append((overlap.item(), N * protrusion.item(), 
        1/N * stretching.item(), 2/N * bending.item(), N * boundary.item()))
    progress_bar.set_description(f"Over. {overlap.item():.2f}, " + 
            f"prot. {protrusion.item():.1f}, " +
            f"stre. {stretching.item():.1f}, " +
            f"bend. {bending.item():.1f}, " +
            f"boun. {boundary.item():.1f}",
            refresh=True)

loss_contributions = {k:list(v) for k, v in 
        zip(['overlap', 'protrusion', 'stretching', 'bending', 'boundary'], zip(*loss_contributions))}

fp.show_3D_configuration(configuration, title='Optimized configuration')

                                                                                                              …

In [12]:
fp.show_losses(loss_contributions)

In [13]:
fp.animate_slices(configuration, radii, domain_radius, title='Optimized configuration')

In [14]:
def analyse_configuration(conf, radii, R):
    '''Various measures of the optimization results'''

    def get_topk_indices(a, k=5):
        k = min(k, a.shape[1]//2)
        _, j = torch.topk(a.flatten(), k)
        j = j.unsqueeze(1)
        return torch.cat((j//a.shape[1], j%a.shape[1]), dim=1)

    def indices_to_coordinates(summary):
        x, y = conf[summary[:,0], :, summary[:,1]].T
        z = summary[:,0]
        if summary.shape[1] == 3:
            x2, y2 = conf[summary[:,0], :, summary[:,2]].T
            x, y, z = torch.stack((x, x2)) , torch.stack((y, y2)), torch.stack((z, z))
        return x, y, z

    conf = conf.detach()
    min_d = fp.minimal_distance(radii)
    d = fp.pairwise_distance(conf)
    overlap_matrix = torch.triu(torch.relu(min_d - d), diagonal=1)
    overlap_indices = torch.nonzero(overlap_matrix)
    overlap_values = overlap_matrix[torch.unbind(overlap_indices, dim=1)]
    overlap_coordinates = indices_to_coordinates(overlap_indices)
  
    protrusion_matrix = torch.relu(conf.norm(dim=-2) + radii - R)
    protrusion_indices = torch.nonzero(protrusion_matrix)
    protrusion_values = protrusion_matrix[torch.unbind(protrusion_indices, dim=1)]
    protrusion_coordinates = indices_to_coordinates(protrusion_indices)

    stretching_matrix = (1/2)**2 * (conf[2:] - 2 * conf[1:-1] 
            + conf[:-2]).pow(2).sum(dim=1)
    stretching_summary = get_topk_indices(stretching_matrix) + torch.tensor([1, 0])
    stretching_coordinates = indices_to_coordinates(stretching_summary)
    
    bending_matrix = (1/6)**2 * (- conf[4:] + 4 * conf[3:-1] - 6 * conf[2:-2] 
            + 4 * conf[1:-3] - conf[:-4]).pow(2).sum(dim=1)
    
    bending_summary = get_topk_indices(bending_matrix) + torch.tensor([2, 0])
    bending_coordinates = indices_to_coordinates(bending_summary)

    analysis = {
        'overlap_indices': overlap_indices,
        'overlap_values': overlap_values,
        'overlap_coordinates': overlap_coordinates,
        'protrusion_indices': protrusion_indices,
        'protrusion_values': protrusion_values,
        'protrusion_coordinates': protrusion_coordinates,
        'stretching_coordinates': stretching_coordinates,
        'stretching_summary': stretching_summary,
        'bending_coordinates': bending_coordinates,
        'bending_summary': bending_summary
    } 
    return analysis
 
analysis = analyse_configuration(configuration, radii, domain_radius)

In [15]:
colors = fp.COLORS

def show_3D_configuration_analysis(configuration, title=None, show=True):
    configuration = configuration.detach()
    Z, _, N = configuration.shape
    x, y = configuration.transpose(0, 1).detach()
    z = torch.arange(Z).view((-1, 1)).repeat((1, N))
    fig = go.Figure()
    for i in range(N):
        fig.add_trace(go.Scatter3d(
            x=x[:, i], y=y[:, i], z=z[:, i],
            line_color='gray', opacity=0.25,
            mode='lines', line=dict(width=4)))

    lx, ly, lz = analysis['overlap_coordinates']
    cx, cy, cz = lx.mean(dim=0), ly.mean(dim=0), lz[0]
    sv = analysis['overlap_values']
    for i in range(len(sv)):
        s = 0.5 * sv[i] / ((lx[0,i] - lx[1,i])**2 + (ly[0,i] - ly[1,i])**2)**0.5
        dx, dy = (lx[1,i] - lx[0,i]) * s, (ly[1,i] - ly[0,i]) * s
        #fig.add_trace(go.Scatter3d(x=lx[:,i], y=ly[:,i], z=lz[:,i], mode='lines', line=dict(width=2, color='yellow')))
        fig.add_trace(go.Scatter3d(x=[cx[i]+dx, cx[i]-dx], y=[cy[i]+dy, cy[i]-dy], z=[cz[i],cz[i]], mode='lines', line=dict(width=3, color='white')))
        fig.add_trace(go.Scatter3d(x=[cx[i]+dx, cx[i]-dx], y=[cy[i]+dy, cy[i]-dy], z=[cz[i],cz[i]], mode='lines', line=dict(width=3, color='black')))
    fig.add_trace(go.Scatter3d(x=cx, y=cy, z=cz, mode='markers', opacity=0.75, marker={'color':sv, 'size':sv*20, 'symbol':'circle'}))

    cx, cy, cz = analysis['protrusion_coordinates']
    sv = analysis['protrusion_values']
    fig.add_trace(go.Scatter3d(x=cx, y=cy, z=cz, mode='markers', marker={'color':'black', 'size':2, 'symbol':'square'}))
    fig.add_trace(go.Scatter3d(x=cx, y=cy, z=cz, mode='markers', opacity=0.75, marker={'color':sv, 'size':sv*100, 'symbol':'square'}))

    for i in analysis['stretching_summary'][:, 1]:
        fig.add_trace(go.Scatter3d(x=x[:, i], y=y[:, i], z=z[:, i], 
            line_color = 'blue', opacity=0.5,
            mode='lines', line=dict(width=6)))

    cx, cy, cz = analysis['stretching_coordinates']
    fig.add_trace(go.Scatter3d(x=cx, y=cy, z=cz, mode='markers', opacity=0.75, marker={'color':'blue', 'symbol':'cross'}))
    
    for i in analysis['bending_summary'][:, 1]:
        fig.add_trace(go.Scatter3d(x=x[:, i], y=y[:, i], z=z[:, i], 
            line_color = 'red', opacity=0.5,
            mode='lines', line=dict(width=6)))

    cx, cy, cz = analysis['bending_coordinates']
    fig.add_trace(go.Scatter3d(x=cx, y=cy, z=cz, mode='markers', opacity=0.75, marker={'color':'red', 'symbol':'cross'}))


    fig.update_layout(scene=dict(xaxis_title='X', yaxis_title='Y',
        zaxis_title='Z', aspectmode='cube'), showlegend=False,
        width=800, height=800)
    fig.show()


fig = show_3D_configuration_analysis(configuration, show=False)


In [16]:
fp.animate_slices(configuration, radii, domain_radius, title='Optimized configuration')

In [17]:
configuration.shape

torch.Size([20, 2, 280])

In [18]:
analysis['overlap_values'].shape

torch.Size([134])

In [19]:
def fix_radii(conf, radii, R):
    conf = conf.detach()
    min_d = fp.minimal_distance(radii)
    d = fp.pairwise_distance(conf)
    overlap_matrix = torch.triu(torch.relu(min_d - d), diagonal=1).max(dim=0).values
    
    protrusion_matrix = torch.relu(conf.norm(dim=-2) + radii - R).max(dim=0).values
    fix = torch.maximum(overlap_matrix.max(dim=0).values, protrusion_matrix)

    return fix


fix = fix_radii(configuration, radii, domain_radius)
fp.show_distribution(fix, name='Fix')

print((radii**2).sum()  / domain_radius**2)
print(((radii-fix)**2).sum()  / domain_radius**2)



tensor(0.7000)
tensor(0.6826)
